In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/socofing/SOCOFing/Real/171__M_Left_little_finger.BMP
/kaggle/input/socofing/SOCOFing/Real/463__F_Right_ring_finger.BMP
/kaggle/input/socofing/SOCOFing/Real/470__F_Right_ring_finger.BMP
/kaggle/input/socofing/SOCOFing/Real/367__M_Left_index_finger.BMP
/kaggle/input/socofing/SOCOFing/Real/446__M_Right_index_finger.BMP
/kaggle/input/socofing/SOCOFing/Real/349__M_Left_index_finger.BMP
/kaggle/input/socofing/SOCOFing/Real/127__F_Left_middle_finger.BMP
/kaggle/input/socofing/SOCOFing/Real/277__M_Right_ring_finger.BMP
/kaggle/input/socofing/SOCOFing/Real/308__M_Left_ring_finger.BMP
/kaggle/input/socofing/SOCOFing/Real/334__F_Left_thumb_finger.BMP
/kaggle/input/socofing/SOCOFing/Real/20__M_Right_little_finger.BMP
/kaggle/input/socofing/SOCOFing/Real/26__M_Right_thumb_finger.BMP
/kaggle/input/socofing/SOCOFing/Real/86__M_Left_middle_finger.BMP
/kaggle/input/socofing/SOCOFing/Real/431__M_Left_ring_finger.BMP
/kaggle/input/socofing/SOCOFing/Real/434__M_Left_thumb_finger.BMP
/kaggle/

KeyboardInterrupt: 

In [2]:
import numpy as np
import pandas as pd
import seaborn as sns
import tensorflow as tf

import os
import cv2
import random

import matplotlib.pyplot as plt

/opt/conda/lib/python3.10/site-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.23.5
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


In [3]:
from tensorflow.keras.models import Sequential,Model
from tensorflow.keras.layers import Dense, Dropout,Activation, Flatten, Conv2D, MaxPool2D
from tensorflow.keras.utils import to_categorical # convert to one-hot-encoding
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.optimizers import RMSprop
from tensorflow.keras.callbacks import ModelCheckpoint, EarlyStopping, ReduceLROnPlateau

from sklearn.model_selection import train_test_split

In [4]:
def extract_label(img_path,train = True):
    filename, _ = os.path.splitext(os.path.basename(img_path))

    subject_id, etc = filename.split('__')
    
    if train:
        gender, lr, finger, _, _ = etc.split('_')
    else:
        gender, lr, finger, _ = etc.split('_')
    
    gender = 0 if gender == 'M' else 1
    lr = 0 if lr == 'Left' else 1
    
    return np.array([subject_id, gender], dtype=np.uint16)

In [5]:
img_size = 96

def loading_data(path,train):
    print("loading data from: ",path)
    data = []
    for img in os.listdir(path):
        try:
            img_array = cv2.imread(os.path.join(path, img), cv2.IMREAD_GRAYSCALE)
            img_resize = cv2.resize(img_array, (img_size, img_size))
            label = extract_label(os.path.join(path, img),train)
            data.append([label[1], img_resize ])
        except Exception as e:
            pass
    data
    return data

In [8]:
Real_path = "/kaggle/input/socofing/SOCOFing/Real"
Easy_path = "/kaggle/input/socofing/SOCOFing/Altered/Altered-Easy"
Medium_path = "/kaggle/input/socofing/SOCOFing/Altered/Altered-Medium"
Hard_path = "/kaggle/input/socofing/SOCOFing/Altered/Altered-Hard"

Easy_data = loading_data(Easy_path, train = True)
Medium_data = loading_data(Medium_path, train = True)
Hard_data = loading_data(Hard_path, train = True)
test = loading_data(Real_path, train = False)

data = np.concatenate([Easy_data, Medium_data, Hard_data], axis=0)

del Easy_data, Medium_data, Hard_data

loading data from:  /kaggle/input/socofing/SOCOFing/Altered/Altered-Easy
loading data from:  /kaggle/input/socofing/SOCOFing/Altered/Altered-Medium
loading data from:  /kaggle/input/socofing/SOCOFing/Altered/Altered-Hard
loading data from:  /kaggle/input/socofing/SOCOFing/Real


<__array_function__ internals>:180: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.


In [9]:
X, y = [], []

for label, feature in data:
    X.append(feature)
    y.append(label)
    
del data

X = np.array(X).reshape(-1, img_size, img_size, 1)
X = X / 255.0

y = np.array(y)

In [10]:
X_test, y_test = [], []

for label, feature in test:
    X_test.append(feature)
    y_test.append(label)
    
del test    
X_test = np.array(X_test).reshape(-1, img_size, img_size, 1)
X_test = X_test / 255.0

y_test = np.array(y_test)

In [11]:
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2, random_state=1)

In [12]:
model = Sequential()

model.add(Conv2D(filters = 32, kernel_size = (5,5),padding = 'Same', 
                 activation ='relu', input_shape = (96,96,1)))
model.add(Conv2D(filters = 32, kernel_size = (5,5),padding = 'Same', 
                 activation ='relu'))
model.add(MaxPool2D(pool_size=(2,2)))
model.add(Dropout(0.25))


model.add(Conv2D(filters = 64, kernel_size = (3,3),padding = 'Same', 
                 activation ='relu'))
model.add(Conv2D(filters = 64, kernel_size = (3,3),padding = 'Same', 
                 activation ='relu'))
model.add(MaxPool2D(pool_size=(2,2), strides=(2,2)))
model.add(Dropout(0.25))


model.add(Flatten())
model.add(Dense(100, activation = "relu"))
model.add(Dropout(0.5))
model.add(Dense(1, activation = "sigmoid"))

In [14]:
epochs = 15 # Turn epochs to 30 to get 0.9967 accuracy
batch_size = 32
model_path = 'Model/model.h5'


model.compile(optimizer = 'adam' , loss = "binary_crossentropy", metrics=["accuracy"])

callbacks = [
    EarlyStopping(monitor='val_acc', patience=20, mode='max', verbose=1),
    ModelCheckpoint(model_path, monitor='val_acc', save_best_only=True, mode='max', verbose=1),
    ReduceLROnPlateau(factor=0.1, patience=5, min_lr=0.00001, verbose=1)
]


history = model.fit(X_train, y_train, batch_size = batch_size, epochs = epochs, 
          validation_data = (X_val, y_val), verbose = 1, callbacks= callbacks)

Epoch 1/15
1232/1232 [==============================] - 1852s 2s/step - loss: 0.4675 - accuracy: 0.8007 - val_loss: 0.4364 - val_accuracy: 0.7993 - lr: 0.0010
Epoch 2/15
1232/1232 [==============================] - 1878s 2s/step - loss: 0.4161 - accuracy: 0.8046 - val_loss: 0.3692 - val_accuracy: 0.8267 - lr: 0.0010
Epoch 3/15
1232/1232 [==============================] - 1873s 2s/step - loss: 0.3508 - accuracy: 0.8335 - val_loss: 0.3033 - val_accuracy: 0.8634 - lr: 0.0010
Epoch 4/15
1232/1232 [==============================] - 1866s 2s/step - loss: 0.2830 - accuracy: 0.8749 - val_loss: 0.2096 - val_accuracy: 0.9102 - lr: 0.0010
Epoch 5/15
1232/1232 [==============================] - 1857s 2s/step - loss: 0.2317 - accuracy: 0.9049 - val_loss: 0.1571 - val_accuracy: 0.9489 - lr: 0.0010
Epoch 6/15
1232/1232 [==============================] - 1844s 1s/step - loss: 0.1912 - accuracy: 0.9250 - val_loss: 0.1185 - val_accuracy: 0.9706 - lr: 0.0010
Epoch 7/15
1232/1232 [========================

In [16]:
layer_name = "dense"
feature_model = Model(inputs=model.input, outputs=model.get_layer(layer_name).output)

In [17]:
X_feature_train=feature_model.predict(X_train)


1232/1232 [==============================] - 369s 300ms/step


In [18]:
from keras.models import model_from_json

model_json = model.to_json()
with open("model.json", "w") as json_file:
    json_file.write(model_json)

model.save("model.h5")
print("Saved model to disk")

Saved model to disk


In [19]:
history_dict = {
    "accuracy": history.history["accuracy"],
    "loss": history.history["loss"],
    "val_accuracy": history.history["val_accuracy"],
    "val_loss": history.history["val_loss"],
}

np.save("history.npy", history_dict)